In [1]:
import json
base_dir = "./outputs/"
dataset_nam = "t_vllm_tiny_test_single_template_single_out_date_00_00_March_03_2025_n_0_6.json"

dataset_name = base_dir + dataset_nam
# Open and read the JSON file
with open(dataset_name, 'r') as file:
    data_1 = json.load(file)


data_11 = data_1 




In [9]:
template = """
{
	"Personal_Information": {
		"Person": {
			"Name": "",
			"National_ID": "",
			"Passport_Number": "",
			"Social_Security_Number": "",
			"Birth_Date": "",
			"Age": "",
			"Height": "",
			"Weight": "",
			"Gender": "",
			"Marital_Status": "",
			"Number_of_Children": "",
			"Nationality_Citizenship": "",
			"Place_of_Birth": "",
			"Mother's_Maiden_Name": "",
			"Race_Ethnic": "",
			"Religion": "",
			"Philosophical_Belief": "",
			"Political_Affiliation": "",
			"Trade_Union_Affiliation": "",
			"Sexual_Preference": "",
			"Sex_Life": ""
		},
		"Appearance": {
			"Picture_of_Face": "",
			"Distinguishing_Characteristic": ""
		},
		"Contact_Information": {
			"Home_Address": {
				"Street_Address": "",
				"City": "",
				"State": "",
				"ZIP_Code": "",
				"Country": ""
			},
			"Phone_Number": "",
			"Email_Address": "",
			"Family_Friend_Contact_Information": ""
		},
		"Online_Identifiers": {
			"Screen_Name": "",
			"Social_Network_Profile": "",
			"Social_Network_Activity": "",
			"URLs": "",
			"Online_Identifiers": ""
		},
		"Location_Information": {
			"Home_Town_City": "",
			"Geographical_Indicators": "",
			"Geo_Location": "",
			"Country": "",
			"ZIP_Code": "",
			"Address": "",
			"Date_Time": ""
		}
	},
	"Work_Information": {
		"Job_Title": "",
		"Occupation": "",
		"Work_ID": "",
		"Work_Address": {
			"Street_Address": "",
			"City": "",
			"State": "",
			"ZIP_Code": "",
			"Country": ""
		},
		"Work_Contact_Information": {
			"Work_Phone_Number": "",
			"Work_Email_Address": ""
		},
		"Employment_Information": {
			"Employment_Status": "",
			"Work_Experience": "",
			"Skills": "",
			"Education": ""
		},
		"Income_Level": ""
	},
	"Financial_Information": {
		"Banking_Details": {
			"Credit_Card_Number": "",
			"Credit_Score": "",
			"ABA_Routing_Number": "",
			"Bank_Account_Number": "",
			"Individual_Taxpayer_Identification": "",
			"SWIFT_Code": "",
			"Crypto": ""
		},
		"Invoice_Payments": "",
		"Financial_Information": ""
	},
	"Security_Information": {
		"Digital_Signature": "",
		"Password": "",
		"License_Numbers": {
			"Drivers_License_Number": "",
			"Vehicle_Registration_Number": "",
			"License_Plate_Number": ""
		},
		"Biometric_Data": {
			"Fingerprint_Data": "",
			"Voice_Print": "",
			"Handwriting_Sample": "",
			"Physiological_Data": "",
			"Genetic_Data": "",
			"X_Ray": "",
			"Biometric_Data": ""
		}
	},
	"Health_Information": {
		"Health_Insurance_ID": "",
		"Medical_History": "",
		"Physiological_Data": ""
	},
	"Cultural_and_Social_Identity": {
		"Cultural_Social_Identity": "",
		"Shopping_Behavior": "",
		"Survey_Answers": "",
		"Signed_Petitions": "",
		"Activities": "",
		"Law_Enforcement_Records": ""
	}
}
"""

In [10]:
from json_repair import repair_json
def repair_output(in_a):
    if  len(in_a) < 10:
        print(1)
        return ""
    if in_a.count('}') ==  in_a.count('{'):
        return in_a
    elif in_a.count('}') > in_a.count('{'):
        try:
            json.loads("{" + in_a)
            in_a = "{" + in_a
        except:
            try:
                json.loads(in_a[1:])
                in_a = in_a[1:]
            except:
                try:
                    in_a = repair_json(in_a)
                    print("Repaired Output")
                    return in_a
                except:
                    print("Output not recoverable {")
                    return ""
                
        return in_a
    elif in_a.count('}') < in_a.count('{'):
        try:
            json.loads( in_a + "}")
            in_a =  in_a + "}"
        except:
            try:
                json.loads(in_a[:-1])
                in_a = in_a[:-1]
            except:
                #print("Output not recoverable }")
                return ""
                
def define_structure(in_a,template):
    if isinstance(in_a,dict) and 'Criminal_Record' in in_a:
        del in_a['Criminal_Record']
    if in_a.keys() != template.keys():
        print(f"{in_a.keys()}")
        print(f"{template.keys()}" )
        return template
    out = {} 
    for key in template:
        if isinstance(template[key],dict) and isinstance(in_a[key],dict):
            out[key] = define_structure(in_a[key], template[key])
        elif not isinstance(in_a[key], dict) and not isinstance(template[key], dict):
            out[key]  = in_a[key]
        else:
            out[key] = template[key]
    return out
def handle_broken_output(in_a, template):
    in_a = repair_output(in_a)
    try:
        out = define_structure(dict(json.loads(in_a)),dict(json.loads(template)))
    except:
        return template
    return out

def sum_dicts(a,b):
    for i,key in enumerate(b):
        if isinstance(b[key], int):
            a[key] = a[key]+b[key]
        if isinstance(b[key], dict):
            a[key] = sum_dicts(a[key],b[key])
    return a
    
def check_output(dic):
    w = {}
    if not isinstance(dic,dict):
        try:
            dic = dict(json.loads(dic))
        except:
            print("F")
    for key in dic:
        if (key == 'Criminal_Record'):
            continue
        print(dic[key])
        if isinstance(dic[key], dict):
            w[key]=check_output(dic[key])
        else:
            if dic[key] != "":
                w[key]= 1
            else:
                w[key] = 0
    return w       

In [11]:

def get_data(data,template, ID ='', depth = 0):
    if isinstance(data,dict):
        get_data_sub(data,template,ID,depth)
    elif isinstance(data, list):
        get_data_sub_2(data,template,ID,depth)
        
                     
    return

def get_data_sub(data,template, ID ='', depth = 0):
    print("Brrrr")
    for i,dat in enumerate(data):
        ID = dat
        print(dat)
        for da in data[dat]:
            templates_name = ['Template']
            data_name = ["Template"]
            for iii,n in enumerate(templates_name):
                if ID not in out_conv.keys():
                    out_conv[ID] = {}
                    out = handle_broken_output(da['out'][data_name[iii]],templates[iii])
                    out_conv[ID][n] = check_output(out)
                else:
                    if n not in out_conv[ID].keys():
                        out = handle_broken_output(da['out'][data_name[iii]],templates[iii])
                        out_conv[ID][n] = check_output(out)
                    else:    
                        out = check_output(handle_broken_output(da['out'][data_name[iii]],templates[iii]))
                        out_conv[ID][n] = sum_dicts(out_conv[ID][n],out) 
                    
    return

def get_data_sub_2(data,template, ID ='', depth = 0):
    for i,dat in enumerate(data):
            ID = dat['id']
            for ii,da in enumerate(dat['data']):
                    if isinstance(da['out'],str):
                        if ID not in out_conv.keys():
                            out_conv[ID] = {}
                            out = handle_broken_output(da['out'],templates[0])
                            out_conv[ID][templates[0]] = check_output(out)
                        else:
                            if ID not in out_conv[ID].keys():
                                out = handle_broken_output(da['out'],templates[0])
                                out_conv[ID][templates[0]] = check_output(out)
                            else:    
                                out = check_output(handle_broken_output(da['out'],templates[0]))
                                out_conv[ID][templates[0]] = sum_dicts(out_conv[ID][templates[0]],out) 
                    
                    else:
                        if data[i]['result'][ii]['data'] == []: continue
                        for iii,n in enumerate(templates_name):
                            #print(f"{i} {ii} {iii}  {ID}")
                            #print(iii)
                            if ID not in out_conv.keys():
                                out_conv[ID] = {}
                                out = handle_broken_output(data[i]['result'][ii]['data'][iii]['data'],templates[iii])
                                out_conv[ID][n] = check_output(out)
                            else:
                                if n not in out_conv[ID].keys():
                                    out = handle_broken_output(data[i]['result'][ii]['data'][iii]['data'],templates[iii])
                                    out_conv[ID][n] = check_output(out)
                                else:    
                                    out = check_output(handle_broken_output(data[i]['result'][ii]['data'][iii]['data'],templates[iii]))
                                    out_conv[ID][n] = sum_dicts(out_conv[ID][n],out) 
                    
    return


In [12]:
import time
out_conv = {}
templates = [template]

get_data(data_1,templates)


{'Person': {'Name': 'Kiefer Sutherland', 'National_ID': '', 'Passport_Number': '', 'Social_Security_Number': '', 'Birth_Date': '', 'Age': '', 'Height': '', 'Weight': '', 'Gender': '', 'Marital_Status': '', 'Number_of_Children': '', 'Nationality_Citizenship': '', 'Place_of_Birth': '', "Mother's_Maiden_Name": '', 'Race_Ethnic': '', 'Religion': '', 'Philosophical_Belief': '', 'Political_Affiliation': '', 'Trade_Union_Affiliation': '', 'Sexual_Preference': '', 'Sex_Life': ''}, 'Appearance': {'Picture_of_Face': '', 'Distinguishing_Characteristic': ''}, 'Contact_Information': {'Home_Address': {'Street_Address': '', 'City': '', 'State': '', 'ZIP_Code': '', 'Country': ''}, 'Phone_Number': '', 'Email_Address': '', 'Family_Friend_Contact_Information': ''}, 'Online_Identifiers': {'Screen_Name': '', 'Social_Network_Profile': '', 'Social_Network_Activity': '', 'URLs': '', 'Online_Identifiers': ''}, 'Location_Information': {'Home_Town_City': '', 'Geographical_Indicators': '', 'Geo_Location': '', 'Co

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



In [13]:
out_conv = {}
for data in data_11:

    for dat in data['data']:
            if data['id'] not in out_conv:
                print(dat)
                out = handle_broken_output(dat['out'],template)
                print(out)
                out_conv[data['id']] = check_output(out)
            else:
                out = check_output(handle_broken_output(dat['out'],template))
                out_conv[data['id']] = sum_dicts(out_conv[data['id']],out)
    

{'out': '\n{\n\t"Personal_Information": {\n        "Person": {\n            "Name": "Kiefer Sutherland",\n            "National_ID": "",\n            "Passport_Number": "",\n            "Social_Security_Number": "",\n            "Birth_Date": "",\n            "Age": "",\n            "Height": "",\n            "Weight": "",\n            "Gender": "",\n            "Marital_Status": "",\n            "Number_of_Children": "",\n            "Nationality_Citizenship": "",\n            "Place_of_Birth": "",\n            "Mother\'s_Maiden_Name": "",\n            "Race_Ethnic": "",\n            "Religion": "",\n            "Philosophical_Belief": "",\n            "Political_Affiliation": "",\n            "Trade_Union_Affiliation": "",\n            "Sexual_Preference": "",\n            "Sex_Life": ""\n        },\n        "Appearance": {\n            "Picture_of_Face": "",\n            "Distinguishing_Characteristic": ""\n        },\n        "Contact_Information": {\n            "Home_Address": {\

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



In [8]:
output_file = "./outputs/Processed/out_single_single_template_vllm_tiny2.json"

with open(output_file, 'w') as f:
    json.dump(out_conv, f, indent=4)
